In [1]:
import pandas as pd 
import os 
import json

In [2]:
# Import the recording session summary table 
recording_summary = "/Volumes/scratch/andrew.shelton/NPUltra_data/raw_npultra_data/NPUltra_recording_summary.xlsx"
recording_summary_table = pd.read_excel(recording_summary)

# Filter table for sessions of interest  
filtered_sessions = recording_summary_table[
    (recording_summary_table['experiment'] == 'NPUltra_psychedelics') &
    (recording_summary_table['uploaded to CO'] == 'yes')]

filtered_sessions.head()

session  subject_id sex        DOB        DOD  age   rec_date  \
67  2024-05-14_714527      714527   F 2023-11-30 2024-05-22  174 2024-05-14   
68  2024-05-15_714527      714527   F 2023-11-30 2024-05-22  165 2024-05-15   
69  2024-05-16_714789      714789   F 2023-12-01 2024-05-24  173 2024-05-16   
70  2024-05-17_714789      714789   F 2023-12-01 2024-05-24  175 2024-05-17   
71  2024-06-04_717033      717033   M 2023-12-18 2024-06-05  170 2024-06-04   

    recording_age  num_recordings recording_rig        genotype .csv metadata  \
67            166               1          NP.1   Sim1-Cre;Ai32  yes      yes   
68            167               1          NP.1   Sim1-Cre;Ai32  yes      yes   
69            167               1          NP.1   Sim1-Cre;Ai32  yes      yes   
70            168               1          NP.1   Sim1-Cre;Ai32  yes      yes   
71            169               1          NP.1  Tlx3-Cre;Ai167  yes      yes   

   uploaded to CO sorted flags  \
67            yes    yes   NaN   
68            yes    yes   NaN   
69            yes    yes   NaN   
70            yes    yes   NaN   
71            yes    yes   NaN   

                                             data_dir            experiment  \
67  \\allen\aind\scratch\andrew.shelton\NPUltra_da...  NPUltra_psychedelics   
68  \\allen\aind\scratch\andrew.shelton\NPUltra_da...  NPUltra_psychedelics   
69  \\allen\aind\scratch\andrew.shelton\NPUltra_da...  NPUltra_psychedelics   
70  \\allen\aind\scratch\andrew.shelton\NPUltra_da...  NPUltra_psychedelics   
71  \\allen\aind\scratch\andrew.shelton\NPUltra_da...  NPUltra_psychedelics   

    notes  
67    NaN  
68    NaN  
69    NaN  
70    NaN  
71    NaN

In [5]:
# Analysis Table 
# Load and store the postprocessed units table (pkl file) for each session.
# Renaming this units table to "analysis" table to avoid confusion with an existing units table in the NWB file. 

# Iterate through each session folder on VAST for sessions of interest
session_list = filtered_sessions['session'].tolist()
session_list = session_list[:1] # For testing, only take the first session 

for session in range(len(session_list)):
    base_path = "/Volumes/scratch/andrew.shelton/NPUltra_data/raw_npultra_data/"
    session_folder = f"{base_path}{session_list[session]}"

    # Navigate to the processed_data/units/ folder within the session folder 
    if os.path.exists(session_folder):
        units_table_path = os.path.join(session_folder, "processed_data", "units")
        if os.path.exists(units_table_path): 
            #Find filename for units table pickle (exclude units_epochs) 
            units_files = [f for f in os.listdir(units_table_path) if 'units_epoch' in f and 'units_epochs' not in f]
            # Load the units table pickle file if it exists 
            if units_files:
                units_table_file = os.path.join(units_table_path, units_files[0])
                analysis_table = pd.read_pickle(units_table_file)
                print(f"Loaded units table from {units_table_file}")

                # Apply any mods to the units table then store as a new "analysis" table in the nwb 
            else:
                print(f"No units table files found in {units_table_path}.")

        else: 
            print(f"Units folder does not exist in {session_folder}.")
    else:
        print(f"Session folder {session_folder} does not exist.")

analysis_table.head()

# to do - add modifications to analysis table and store. change the value names to analysis table so we don't get confused 
# remove probe_config 

Loaded units table from /Volumes/scratch/andrew.shelton/NPUltra_data/raw_npultra_data/2024-05-14_714527/processed_data/units/2024-05-14_714527_1_units_epoch.pkl


unitID          sessionID  mouseID       genotype experiment  recording  \
0       0  2024-05-14_714527   714527  Sim1-Cre;Ai32     saline          1   
1       2  2024-05-14_714527   714527  Sim1-Cre;Ai32     saline          1   
2       3  2024-05-14_714527   714527  Sim1-Cre;Ai32     saline          1   
3       4  2024-05-14_714527   714527  Sim1-Cre;Ai32     saline          1   
4       5  2024-05-14_714527   714527  Sim1-Cre;Ai32     saline          1   

  recording_date probe                      probe_type probe_config  ...  \
0     2024-05-14     A  Neuropixels Ultra (Switchable)      192 x 2  ...   
1     2024-05-14     A  Neuropixels Ultra (Switchable)      192 x 2  ...   
2     2024-05-14     A  Neuropixels Ultra (Switchable)      192 x 2  ...   
3     2024-05-14     A  Neuropixels Ultra (Switchable)      192 x 2  ...   
4     2024-05-14     A  Neuropixels Ultra (Switchable)      192 x 2  ...   

  optotagged    ct      spread bAP_extent bAP_attenuation    bAP_idx  \
0          1  Sim1  328.182719      138.0        0.946919   7.859134   
1          1  Sim1  212.309379      330.0        0.949073  17.150019   
2          0    RS  383.142452      162.0        0.937089  11.135912   
3          0   FSl  142.123765      102.0        0.947345   5.441735   
4          0    RS  230.484794      156.0        0.947703   8.474708   

  burst_idx num_bursts burst_dur burst_proportion  
0  0.060936      11148  0.006740         0.294797  
1  0.004880        469  0.004328         0.016025  
2  0.017000        170  0.004582         0.055700  
3  0.000000          0       NaN         0.000000  
4  0.000297         10  0.005147         0.000892  

[5 rows x 54 columns]

In [6]:
# Stimulus Table 
# Source the stimulus information from the stimulus table in the processed_data/stim/ folder for each session and the session.json metadata. 

# Iterate through each session folder on VAST for sessions of interest 
session_list = filtered_sessions['session'].tolist()
session_list = session_list[:1] # For testing, taking the first session 

for session in range(len(session_list)):
    base_path = "/Volumes/scratch/andrew.shelton/NPUltra_data/raw_npultra_data/"
    session_folder = f"{base_path}{session_list[session]}"
    # Initialize a new stim table for each session 
    stim_table = pd.DataFrame(columns=['start_time', 'stop_time', 'power', 'stim_name', 'emission_location', 'wavelength'])

    # Load the stimulus table 
    if os.path.exists(session_folder):
        stim_path = os.path.join(session_folder, "processed_data", "stim") 
        if os.path.exists(stim_path): 
            stim_table_path = os.path.join(stim_path, "opto_stim_df.csv")
            if os.path.exists(stim_table_path): 
                opto_stim_df = pd.read_csv(stim_table_path)
                print(f"Loaded stimulus table from {stim_table_path}")
                
                # Store data from opto_stim_df for the new stim_table 
                stim_table['start_time'] = opto_stim_df['stim_on']
                stim_table['stop_time'] = opto_stim_df['stim_off'] 
                stim_table['stim_name'] = opto_stim_df['epoch_label']
                stim_table['emission_location'] = opto_stim_df['probe']
            else:
                print(f"No stimulus table files found in {stim_path}.")
        else:
            print(f"Stimulus folder does not exist in {session_folder}.")

        # Source other stimulus information from the session.json metadata file 
        metadata_path = os.path.join(session_folder, "metadata")
        if os.path.exists(metadata_path):
            metadata_file = os.path.join(metadata_path, "session.json")
            if os.path.exists(metadata_file):
                with open(metadata_file, 'r') as f:
                    metadata = json.load(f)
                    # Extract wavelength and power from session.json 
                    wavelength = None
                    power = None
                    # Loop through the stimulus epochs and extract the wavelength and power from the first light source config group 
                    for epoch in metadata.get('stimulus_epochs', []):
                        light_config = epoch.get('light_source_config')
                        if light_config is not None:
                            wavelength = light_config.get('wavelength')
                            power = light_config.get('laser_power')
                            break  # Use the first epoch with light source config
                    
                    stim_table['wavelength'] = wavelength
                    stim_table['power'] = power
            else:
                print(f"Metadata file does not exist in {metadata_path}.")
        else:
            print(f"Metadata folder does not exist in {session_folder}.") 

    else:
        print(f"Session folder {session_folder} does not exist.")


stim_table.head()

Loaded stimulus table from /Volumes/scratch/andrew.shelton/NPUltra_data/raw_npultra_data/2024-05-14_714527/processed_data/stim/opto_stim_df.csv


start_time   stop_time  power      stim_name emission_location wavelength
0  2473.89271  2473.90471   13.5  OptoTagging_0                 B        488
1  2475.16007  2475.36207   13.5  OptoTagging_0                 F        488
2  2476.36221  2476.37421   13.5  OptoTagging_0                 D        488
3  2477.49455  2477.50656   13.5  OptoTagging_0                 F        488
4  2478.77895  2478.98096   13.5  OptoTagging_0                 D        488

In [ ]:
# Epoch table 
# Construct a new epoch table with epoch names, start times, and stop times from the stimulus tables for each epoch and metadata. 
# This stitches together the trial start/stop times from the CSVs for each stimulus epoch type, then 
# Finds the start/stop times for each epoch and adds injection epochs based on the OptoTagging notes in the session.json metadata file. 

# Iterate through each session folder on VAST for sessions of interest
session_list = filtered_sessions['session'].tolist()
session_list = session_list[:1] # For testing, only take the first session 

# Construct list of session folder paths 
for session in range(len(session_list)): 
    base_path = "/Volumes/scratch/andrew.shelton/NPUltra_data/raw_npultra_data/"
    session_folder = f"{base_path}{session_list[session]}"

    # Check if the session folder exists open the CSVs for each stimulus epoch type 
    if os.path.exists(session_folder):
        epoch_path = os.path.join(session_folder, "processed_data", "stim")
        if os.path.exists(epoch_path): 

            # Initialize list to collect all DataFrames
            all_epoch_data = []
            
            # Process each CSV file 
            epoch_files = [f for f in os.listdir(epoch_path) if f.endswith('.csv')]
            if epoch_files:
                for epoch_file in epoch_files:
                    file_path = os.path.join(epoch_path, epoch_file)
                    
                    # Read only required columns and handle missing stim_off column  
                    try:
                        temp_df = pd.read_csv(file_path, usecols=['stim_on', 'stim_off', 'epoch_label'])
                    except ValueError:
                        # If stim_off doesn't exist in csv, read without it and add NaN column
                        temp_df = pd.read_csv(file_path, usecols=['stim_on', 'epoch_label'])
                        temp_df['stim_off'] = pd.NA
                    
                    # Add to collection
                    all_epoch_data.append(temp_df)
                
                # Combine all data and use groupby
                if all_epoch_data:
                    combined_df = pd.concat(all_epoch_data, ignore_index=True)
                    
                    # Use groupby to process each epoch_label
                    # Only Optotagging epochs will have stim_off, others will use stim_on for stop_time
                    epoch_summary = combined_df.groupby('epoch_label').apply(
                        lambda group: pd.Series({
                            'start_time': group['stim_on'].min(),
                            'stop_time': group['stim_off'].max() if 'OptoTagging' in group.name else group['stim_on'].max()
                        })
                    ).reset_index()
                    
                    # Rename columns to match expected format
                    epoch_table = epoch_summary.rename(columns={'epoch_label': 'stim_name'})

            # Sort table by start_time to maintain temporal order
            epoch_table = epoch_table.sort_values(by='start_time').reset_index(drop=True)

        # In between Optotagging_0 and Spontaneous_1, include a new epoch for the Substance Injection (Saline or Psilocybin) 
        # Load the session.json in the /metadata folder 
        metadata_path = os.path.join(session_folder, "metadata")
        if os.path.exists(metadata_path):
            metadata_file = os.path.join(metadata_path, "session.json")
            if os.path.exists(metadata_file):
                with open(metadata_file, 'r') as f:
                    metadata = json.load(f)

                # The note in the OptoTagging stimulus epoch indicates if Saline or Psilocybin was injected 
                for epoch in metadata.get('stimulus_epochs', []):
                    if epoch.get('stimulus_name') == 'OptoTagging':
                        notes = epoch.get('notes', '')
                        
                        if 'Saline' in notes: 
                            injection_name = "Saline_Injection' 
                            
                        elif 'Psilocybin' in notes: 
                            injection_name = "Psilocybin_Injection" 

                        else: 
                            print(f"No injection note found in OptoTagging epoch for {session_list[session]}.")
                            injection_name = "Injection" 

                            # Use the OptoTaggin_0 stop time and Spontaneous_1 start time to create a new epoch for the injection  
                            opto_0_stop = None
                            spont_1_start = None
                            
                            for idx, row in epoch_table.iterrows():
                                if row['stim_name'] == 'OptoTagging_0':
                                    opto_0_stop = row['stop_time']
                                elif row['stim_name'] == 'Spontaneous_1':
                                    spont_1_start = row['start_time']
                            
                            if opto_0_stop is not None and spont_1_start is not None:
                                # Create injection epoch with 0.01 value difference from OptoTagging_0 and Spontaneous_1
                                injection_start = opto_0_stop + 0.01
                                injection_end = spont_1_start - 0.01
                                
                                # Find insertion point (after OptoTagging_0, before Spontaneous_1)
                                insert_idx = None
                                for idx, row in epoch_table.iterrows():
                                    if row['stim_name'] == 'OptoTagging_0':
                                        insert_idx = idx + 1
                                        break
                                
                                # Create new row
                                new_row = pd.DataFrame({
                                    'stim_name': [injection_name],
                                    'start_time': [injection_start],
                                    'stop_time': [injection_end]
                                })
                                
                                # Insert the new row at the correct position
                                if insert_idx is not None:
                                    epoch_table = pd.concat([
                                        epoch_table.iloc[:insert_idx],
                                        new_row,
                                        epoch_table.iloc[insert_idx:]
                                    ], ignore_index=True)
                                    print(f"Added {injection_name} epoch from {injection_start} to {injection_end}")
                            
                            break  # Only process first OptoTagging epoch with injection note
            else:
                print(f"Metadata file does not exist in {metadata_path}.")
        else:
            print(f"Metadata folder does not exist in {session_folder}.") 

epoch_table

Added Saline_Injection epoch from 2714.53929 to 3058.6834599999997


stim_name  start_time     stop_time
0      Spontaneous_0    47.95425   1249.948000
1        RFMapping_0  1259.78593   2461.428177
2      OptoTagging_0  2473.89271   2714.529290
3   Saline_Injection  2714.53929   3058.683460
4      Spontaneous_1  3058.69346   4260.504159
5        RFMapping_1  4270.54235   5472.251517
6      OptoTagging_1  5484.66564   5723.199880
7      Spontaneous_2  5734.03576   6935.628960
8        RFMapping_2  6945.66720   8147.458768
9      OptoTagging_2  8159.97412   8399.791680
10     Spontaneous_3  8703.18912   9304.162709
11       RFMapping_3  9313.71705   9914.855879
12     Spontaneous_4  9986.38065  10587.321079

In [ ]:
# other to do
# pull out the units table within the nwb and make any mods if necessary (don't have any requests to change this yet...) 
# create a stimulus template 
# once those items are done, refactor this into a bunch of functions so i can pass several data folders through this efficiently... 
# metadata mods 
# upload new assets via data transfer service under new project name (NP Ultra Psychedelics)
# vocab fixes 

# finished 
# create a stimulus table x
# add code to save/store the modified tables somewhere x
# modify nwbs... x


In [ ]:
# The code below works
# clean up
# epoch table, want to unpack the string that gets stored into the stim_name column 
# double check that the outputs are accurate, in particular the processed_units table x (from_dataframe cleans this up a lot)
# double check the vocabulary of everything 
# clean up and refactor into a set of functions so that we can process many files and store 

In [ ]:
import hdmf_zarr
from hdmf.common import DynamicTable
# from hdmf.common.table import VectorData # comment out? 
# from pynwb.epoch import TimeIntervals # comment out? 
import numpy as np
import pandas as pd
import os

def convert_dataframe_to_dynamic_table(df, table_name):
    """Convert pandas DataFrame to DynamicTable using built-in method."""
    
    # Convert pandas DataFrame to DynamicTable using hdmf's built-in method 
    dynamic_table = DynamicTable.from_dataframe(
        name=table_name.lower().replace(' ', '_'), # Ensures input is lowercase and has underscores 
        df=df
    )
    
    print(f"Created DynamicTable '{table_name}' with {len(df)} rows and {len(df.columns)} columns")
    
    return dynamic_table

def add_tables_to_nwb_zarr(nwb_path, new_nwb_path, analysis_table=None, stim_table=None, epoch_table=None):
    """Add tables to existing nwb file and exports new, modified nwb file"""
    
    # Create directory for new file
    os.makedirs(os.path.dirname(new_nwb_path), exist_ok=True)
    
    # Open existing NWB file 
    io = hdmf_zarr.NWBZarrIO(nwb_path, mode="r")
    nwbfile = io.read()
    
    # Add analysis table using add_analysis 
    if analysis_table is not None:
        print("Processing analysis table...")
        try:
            # Convert analysis table (df) to DynamicTable 
            analysis_dynamic_table = convert_dataframe_to_dynamic_table(
                df=analysis_table,
                table_name="processed_units"
                )
            # Add DynamicTable to analysis container 
            nwbfile.add_analysis(analysis_dynamic_table)
            print(f"Added analysis table with {len(analysis_table)} rows")
        except Exception as e:
            print(f"Failed to add analysis table: {e}")
            raise
    
    # Add stimulus table using add_stimulus 
    if stim_table is not None:
        print("Processing stimulus table...")
        try:
            # Convert stimulus table (df) to DynamicTable
            stimulus_dynamic_table = convert_dataframe_to_dynamic_table(
                df=stim_table,
                table_name="optogenetic_stimuli"
                )
            # Add DynamicTable to stimulus container 
            nwbfile.add_stimulus(stimulus_dynamic_table)
            print(f"Added stimulus table with {len(stim_table)} rows")
        except Exception as e:
            print(f"Failed to add stimulus table: {e}")

            # Print traceback for debugging if table creation fails 
            import traceback
            traceback.print_exc()
            raise
    
    # Create and add epoch table using add_epoch 
    if epoch_table is not None:
        print("Processing epoch table...")
        try:
            # Construct epoch table row by row 
            for idx, row in epoch_table.iterrows():
                tags = [str(row['stim_name'])] if 'stim_name' in row and pd.notna(row['stim_name']) else []
                nwbfile.add_epoch(
                    start_time=float(row['start_time']),
                    stop_time=float(row['stop_time']),
                    tags=tags
                )
            print(f"Added {len(epoch_table)} epochs")
        except Exception as e:
            print(f"Failed to add epoch table: {e}")
            raise
    
    # Write to new file
    with hdmf_zarr.NWBZarrIO(new_nwb_path, mode='w') as export_io:
        export_io.export(src_io=io, nwbfile=nwbfile)
    
    io.close()
    print(f"Saved to: {new_nwb_path}")
    
# Usage
def process_nwb_file(original_path, new_path, analysis_df=None, stimulus_df=None, epochs_df=None):
    """Simple wrapper function."""
    add_tables_to_nwb_zarr(
        nwb_path=original_path,
        new_nwb_path=new_path,
        analysis_table=analysis_df,
        stim_table=stimulus_df,
        epoch_table=epochs_df
    )

In [ ]:
# Define paths
original_nwb = '/Volumes/scratch/andrew.shelton/NPUltra_data/raw_npultra_data/2024-05-14_714527/20240514_714527_1/ecephys_714527_2024-05-14_13-22-07_experiment1_recording1.nwb'
new_nwb = '/Volumes/scratch/suyee.lee/ecephys_714527_2024-05-14_13-22-07_experiment1_recording1_6.nwb'
# 
# Process the file
process_nwb_file(
    original_path=original_nwb,
    new_path=new_nwb,
    analysis_df=analysis_table,  # Your analysis DataFrame
    stimulus_df=stim_table,      # Your stimulus DataFrame  
    epochs_df=epoch_table        # Your epochs DataFrame
)

Processing analysis table...
Created DynamicTable 'processed_units' with 350 rows and 54 columns
✓ Added analysis table with 350 rows
Processing stimulus table...
Created DynamicTable 'optogenetic_stimuli' with 600 rows and 6 columns
✓ Added stimulus table with 600 rows
Processing epoch table...
✓ Added 13 epochs


/Users/suyee.lee/np-ultra-psychedelics/.venv/lib/python3.12/site-packages/zarr/storage.py:455: FutureWarning: missing object_codec for object array; this will raise a ValueError in version 3.0
  _init_array_metadata(


✓ Saved to: /Volumes/scratch/suyee.lee/ecephys_714527_2024-05-14_13-22-07_experiment1_recording1_6.nwb


In [68]:
# Open the new nwb file and inspect the contents. Should be using NWBZarrIO 
new_nwb = '/Volumes/scratch/suyee.lee/ecephys_714527_2024-05-14_13-22-07_experiment1_recording1_6.nwb'

with hdmf_zarr.NWBZarrIO(new_nwb, mode='r') as io:
    new_nwbfile = io.read()
    print("Loaded new NWB file:", new_nwb)
    print("Processing modules:", list(new_nwbfile.processing.keys()))
    print("Stimulus presentations and epochs:", list(new_nwbfile.stimulus.keys()) if hasattr(new_nwbfile, 'stimulus') else "None")
    print("Epochs:", new_nwbfile.epochs)  # Should show the added epochs
    print("Trials:", new_nwbfile.trials)  # Should show the added trials


Loaded new NWB file: /Volumes/scratch/suyee.lee/ecephys_714527_2024-05-14_13-22-07_experiment1_recording1_6.nwb
Processing modules: []
Stimulus presentations and epochs: ['optogenetic_stimuli']
Epochs: epochs pynwb.epoch.TimeIntervals at 0x5290400304
Fields:
  colnames: ['start_time' 'stop_time' 'tags']
  columns: (
    start_time <class 'hdmf.common.table.VectorData'>,
    stop_time <class 'hdmf.common.table.VectorData'>,
    tags_index <class 'hdmf.common.table.VectorIndex'>,
    tags <class 'hdmf.common.table.VectorData'>
  )
  description: experimental epochs
  id: id <class 'hdmf.common.table.ElementIdentifiers'>

Trials: None


In [70]:
processed_units = new_nwbfile.analysis['processed_units']
processed_units

processed_units hdmf.common.table.DynamicTable at 0x16081740592
Fields:
  colnames: ['unitID' 'sessionID' 'mouseID' 'genotype' 'experiment' 'recording'
 'recording_date' 'probe' 'probe_type' 'probe_config' 'spike_times'
 'Spontaneous_0_spikes' 'Spontaneous_1_spikes' 'Spontaneous_2_spikes'
 'Spontaneous_3_spikes' 'Spontaneous_4_spikes' 'RFMapping_0_spikes'
 'RFMapping_1_spikes' 'RFMapping_2_spikes' 'RFMapping_3_spikes'
 'mean_waveform' 'Spontaneous_0_waveform' 'Spontaneous_1_waveform'
 'Spontaneous_2_waveform' 'Spontaneous_3_waveform'
 'Spontaneous_4_waveform' 'RFMapping_0_waveform' 'RFMapping_1_waveform'
 'RFMapping_2_waveform' 'RFMapping_3_waveform' '10ms_pulse_psth'
 '200ms_pulse_psth' 'amp' 'dur' 'PTR' 'prePTR' 'repol_slope' 'recov_slope'
 'avg_ISI' 'baseline_FR' 'evoked_FR' 'footprint' 'layer' 'region'
 'optotagged' 'ct' 'spread' 'bAP_extent' 'bAP_attenuation' 'bAP_idx'
 'burst_idx' 'num_bursts' 'burst_dur' 'burst_proportion']
  columns: (
    unitID <class 'hdmf.common.table.VectorData'>,
    sessionID <class 'hdmf.common.table.VectorData'>,
    mouseID <class 'hdmf.common.table.VectorData'>,
    genotype <class 'hdmf.common.table.VectorData'>,
    experiment <class 'hdmf.common.table.VectorData'>,
    recording <class 'hdmf.common.table.VectorData'>,
    recording_date <class 'hdmf.common.table.VectorData'>,
    probe <class 'hdmf.common.table.VectorData'>,
    probe_type <class 'hdmf.common.table.VectorData'>,
    probe_config <class 'hdmf.common.table.VectorData'>,
    spike_times_index <class 'hdmf.common.table.VectorIndex'>,
    spike_times <class 'hdmf.common.table.VectorData'>,
    Spontaneous_0_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    Spontaneous_0_spikes <class 'hdmf.common.table.VectorData'>,
    Spontaneous_1_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    Spontaneous_1_spikes <class 'hdmf.common.table.VectorData'>,
    Spontaneous_2_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    Spontaneous_2_spikes <class 'hdmf.common.table.VectorData'>,
    Spontaneous_3_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    Spontaneous_3_spikes <class 'hdmf.common.table.VectorData'>,
    Spontaneous_4_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    Spontaneous_4_spikes <class 'hdmf.common.table.VectorData'>,
    RFMapping_0_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    RFMapping_0_spikes <class 'hdmf.common.table.VectorData'>,
    RFMapping_1_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    RFMapping_1_spikes <class 'hdmf.common.table.VectorData'>,
    RFMapping_2_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    RFMapping_2_spikes <class 'hdmf.common.table.VectorData'>,
    RFMapping_3_spikes_index <class 'hdmf.common.table.VectorIndex'>,
    RFMapping_3_spikes <class 'hdmf.common.table.VectorData'>,
    mean_waveform <class 'hdmf.common.table.VectorData'>,
    Spontaneous_0_waveform <class 'hdmf.common.table.VectorData'>,
    Spontaneous_1_waveform <class 'hdmf.common.table.VectorData'>,
    Spontaneous_2_waveform <class 'hdmf.common.table.VectorData'>,
    Spontaneous_3_waveform <class 'hdmf.common.table.VectorData'>,
    Spontaneous_4_waveform <class 'hdmf.common.table.VectorData'>,
    RFMapping_0_waveform <class 'hdmf.common.table.VectorData'>,
    RFMapping_1_waveform <class 'hdmf.common.table.VectorData'>,
    RFMapping_2_waveform <class 'hdmf.common.table.VectorData'>,
    RFMapping_3_waveform <class 'hdmf.common.table.VectorData'>,
    10ms_pulse_psth <class 'hdmf.common.table.VectorData'>,
    200ms_pulse_psth <class 'hdmf.common.table.VectorData'>,
    amp <class 'hdmf.common.table.VectorData'>,
    dur <class 'hdmf.common.table.VectorData'>,
    PTR <class 'hdmf.common.table.VectorData'>,
    prePTR <class 'hdmf.common.table.VectorData'>,
    repol_slope <class 'hdmf.common.table.VectorData'>,
    recov_slope <class 'hdmf.common.table.VectorData'>,
    avg_ISI <class 'hdmf.common.table.VectorData'>,
    baseline_FR <class 'hdmf.comm

In [72]:
processed_units_df = processed_units.to_dataframe()

In [83]:
epochs= new_nwbfile.epochs.to_dataframe()
epochs

start_time     stop_time                tags
id                                              
0     47.95425   1249.948000     [Spontaneous_0]
1   1259.78593   2461.428177       [RFMapping_0]
2   2473.89271   2714.529290     [OptoTagging_0]
3   2714.53929   3058.683460  [Saline_Injection]
4   3058.69346   4260.504159     [Spontaneous_1]
5   4270.54235   5472.251517       [RFMapping_1]
6   5484.66564   5723.199880     [OptoTagging_1]
7   5734.03576   6935.628960     [Spontaneous_2]
8   6945.66720   8147.458768       [RFMapping_2]
9   8159.97412   8399.791680     [OptoTagging_2]
10  8703.18912   9304.162709     [Spontaneous_3]
11  9313.71705   9914.855879       [RFMapping_3]
12  9986.38065  10587.321079     [Spontaneous_4]

In [84]:
stimulus_presentation = new_nwbfile.stimulus['optogenetic_stimuli'].to_dataframe()
stimulus_presentation

start_time   stop_time  power      stim_name emission_location wavelength
id                                                                            
0    2473.89271  2473.90471   13.5  OptoTagging_0                 B        488
1    2475.16007  2475.36207   13.5  OptoTagging_0                 F        488
2    2476.36221  2476.37421   13.5  OptoTagging_0                 D        488
3    2477.49455  2477.50656   13.5  OptoTagging_0                 F        488
4    2478.77895  2478.98096   13.5  OptoTagging_0                 D        488
..          ...         ...    ...            ...               ...        ...
595  8394.75281  8394.95482   13.5  OptoTagging_2                 B        488
596  8395.88706  8396.08906   13.5  OptoTagging_2                 D        488
597  8397.18767  8397.19967   13.5  OptoTagging_2                 A        488
598  8398.32362  8398.33562   13.5  OptoTagging_2                 B        488
599  8399.58967  8399.79168   13.5  OptoTagging_2                 F        488

[600 rows x 6 columns]